In [118]:
from repositories import csvTRNSYS
import pandas as pd
import datetime
import matplotlib.pyplot as plt
from sqlalchemy import create_engine
from utils import comfortValues, comfortGraph, transformation_EP_CO2
from utils.transformation_EP_CO2 import pE_ARV_demand, CO2_ARV_demand, calculo
pd.set_option('display.max_rows', 100)  # Change 10 to the desired number of rows



In [112]:
!  c.NotebookApp.iopub_data_rate_limit = 10000000  # Set a higher limit (e.g., 10 MB/s)

"c.NotebookApp.iopub_data_rate_limit" no se reconoce como un comando interno o externo,
programa o archivo por lotes ejecutable.


In [142]:
n_zones = 1
name = 'FE35'
n_viv = 1
typeStep = csvTRNSYS.HourlyMulti() 
output = csvTRNSYS.readTRNSYS(typeStep, n_viv, name)
output_reader, P_ht, P_cl, P_lig, P_dev, P_dhw = output.start()
grado_ht = {'joule':0.32,'BC':0.31,'caldera_GN':0.27,'butano':0.06,'nada':0.04}
grado_cl = {'split':0.1,'BC':0.43,'multi_split':0.04,'nada':0.43}
grado_dhw ={'caldera_GN':0.86,'butano':0.14,'BC':0}
coef_CO2={'ele': 0.331, 'GN': 0.252, 'butano': 0.254}
coef_NRPE={'ele': 1.954, 'GN': 1.190, 'butano': 1.201}
EER = 2
COP=2 
COP_DHW=1.7 
eta_cal=0.7
P_ht

{'BC0_0': {'Dwelling_1': [0.0,
   0.013943688146161613,
   0.01577031613303688,
   0.015819811390408996,
   0.015262582061859575,
   0.003969653372767092,
   0.011340362627703519,
   0.020114567865391297,
   0.019796338209640354,
   0.019423308729197553,
   0.006159056495354009,
   0.02132221598859055,
   0.018153159352215186,
   0.01990158574761529,
   0.020288732079677383,
   0.020415484009152017,
   0.021187196336462624,
   0.008494705026428389,
   0.022538150835669398,
   0.011442719594427922,
   0.019686792225199472,
   0.023079678982251193,
   0.004740259417732996,
   0.02649759524514946,
   0.025620596797737726,
   0.028044397317894484,
   0.029340261868487767,
   0.03308944416212284,
   0.0336445562981299,
   0.020026010035809286,
   0.02269394244174368,
   0.015307983689162696,
   0.037593452154285945,
   0.016632246840402064,
   0.044663455064613694,
   0.03536051282192552,
   0.03287900831318343,
   0.03360468190453456,
   0.034275662684190085,
   0.03298638995618194,
   0.0

In [149]:

def calculate_PE_ht(P_ht, grado_ht, COP, coef_NRPE, eta_cal):
    PE_ht_ = {}

    for i in P_ht:
        PE_ht_.setdefault(i, [])
        count = 0
        for j in range(len(P_ht[i])):
            key_exists = True
            # Check if the keys exist in grado_ht before accessing them
            for key in ['joule', 'BC', 'caldera_GN', 'butano', 'nada']:
                if key not in grado_ht:
                    key_exists = False
                    break

            if key_exists:
                PE_value = P_ht[i][count] * (
                    ((grado_ht['joule'] + grado_ht['BC']) / COP) * coef_NRPE['ele'] +
                    ((grado_ht['caldera_GN'] + grado_ht['nada']) / eta_cal * coef_NRPE['GN']) +
                    (grado_ht['butano'] / eta_cal * coef_NRPE['butano'])
                )
                PE_ht_[i].append(PE_value)
            else:
                pass

            count += 1

    return PE_ht_

result = calculate_PE_ht(P_ht, grado_ht, COP, coef_NRPE, eta_cal)



result = calculate_PE_ht(grado_ht, COP, coef_NRPE, eta_cal)




TypeError: can't multiply sequence by non-int of type 'float'

In [108]:
pe_arv_demand = pE_ARV_demand(grado_ht, grado_cl, grado_dhw,)
co2_arv_demand = CO2_ARV_demand(grado_ht, grado_cl, grado_dhw, coef_CO2)

In [109]:
calculation = calculo(pe_arv_demand, P_ht, P_cl, P_lig, P_dev, P_dhw)

In [110]:
results = calculation.start()



KeyError: 0

In [ ]:

# Instancia de la clase para pasar de demanda a consumo de energía primaria.

In [122]:

PE_ht = {}
PE_cl = {}
PE_lig = {}
PE_dev = {}
PE_dhw = {}

project = transformation_EP_CO2.pE_ARV_demand(grado_ht, grado_cl, grado_dhw)
for i in P_ht:
    output = transformation_EP_CO2.calculo(project, P_ht[i], P_cl[i], P_lig[i],P_dev[i],P_dhw[i])
    PE_ht_aux, PE_cl_aux, PE_lig_aux,PE_dev_aux ,PE_dhw_aux = output.start()
    PE_ht.setdefault(i, PE_ht_aux)
    PE_cl.setdefault(i, PE_cl_aux)
    PE_lig.setdefault(i, PE_lig_aux)
    PE_dev.setdefault(i,PE_dev_aux)
    PE_dhw.setdefault(i, PE_dhw_aux)


In [128]:
PE_ht = pd.DataFrame(PE_ht)
PE_ht

BC0_0  \
Dwelling_1  [0.0, 0.021725560902761936, 0.0245716169217695...   

                                                      BC0_180  \
Dwelling_1  [0.0, 0.021725560902761936, 0.0245716169217695...   

                                                      BC0_270  \
Dwelling_1  [0.0, 0.021725560902761936, 0.0245716169217695...   

                                                       BC0_90  \
Dwelling_1  [0.0, 0.021725560902761936, 0.0245716169217695...   

                                                P111_0_W8_R10  \
Dwelling_1  [0.0, 0.02171474307260574, 0.02437654057169146...   

                                                P111_0_W8_R12  \
Dwelling_1  [0.0, 0.02171474300342184, 0.02437653182694835...   

                                                P111_0_W8_R14  \
Dwelling_1  [0.0, 0.021714742973846766, 0.0243765289541458...   

                                                 P111_0_W8_R6  \
Dwelling_1  [0.0, 0.02171474466696584, 0.02437664597921095...   

                                                 P111_0_W8_R8  \
Dwelling_1  [0.0, 0.021714743391190037, 0.0243765671370249...   

                                              P111_180_W8_R10  ...  \
Dwelling_1  [0.0, 0.02171474307260574, 0.02437654057169146...  ...   

                                                P221_90_W6_R5  \
Dwelling_1  [0.0, 0.017406750286469888, 0.0192652747722053...   

                                                P221_90_W8_R5  \
Dwelling_1  [0.0, 0.01740675028022831, 0.01926527340351150...   

                                                 P222_0_W6_R5  \
Dwelling_1  [0.0, 0.017406750055917755, 0.0192652642072097...   

                                                 P222_0_W8_R5  \
Dwelling_1  [0.0, 0.01740675004967615, 0.01926526283851584...   

                                               P222_180_W6_R5  \
Dwelling_1  [0.0, 0.017406750055917755, 0.0192652642072097...   

                                               P222_180_W8_R5  \
Dwelling_1  [0.0, 0.01740675004967615, 0.01926526283851584...   

                                               P222_270_W6_R5  \
Dwelling_1  [0.0, 0.017406750055917755, 0.0192652642072097...   

                                               P222_270_W8_R5  \
Dwelling_1  [0.0, 0.01740675004967615, 0.01926526283851584...   

                                                P222_90_W6_R5  \
Dwelling_1  [0.0, 0.017406750055917755, 0.0192652642072097...   

                                                P222_90_W8_R5  
Dwelling_1  [0.0, 0.01740675004967615, 0.01926526283851584...  

[1 rows x 84 columns]

In [129]:
heating_consumption = pd.concat([PE_ht[col].explode().reset_index(drop=True) for col in PE_ht.columns],axis=1)
heating_consumption

BC0_0   BC0_180   BC0_270    BC0_90 P111_0_W8_R10 P111_0_W8_R12  \
0          0.0       0.0       0.0       0.0           0.0           0.0   
1     0.021726  0.021726  0.021726  0.021726      0.021715      0.021715   
2     0.024572  0.024572  0.024572  0.024572      0.024377      0.024377   
3     0.024649  0.024649  0.024649  0.024649      0.023799      0.023798   
4     0.023781  0.023781  0.023781  0.023781       0.02195      0.021949   
...        ...       ...       ...       ...           ...           ...   
8755  0.050948  0.050379  0.045257  0.039275      0.030691      0.030004   
8756  0.050232  0.050045  0.045085   0.03975      0.031247      0.030579   
8757  0.048674   0.04863  0.044052  0.039064      0.030474      0.029823   
8758  0.049046  0.049038  0.045067  0.040434      0.031839      0.031227   
8759  0.051975  0.051971  0.048234  0.043648      0.034076      0.033452   

     P111_0_W8_R14 P111_0_W8_R6 P111_0_W8_R8 P111_180_W8_R10  ...  \
0              0.0          0.0          0.0             0.0  ...   
1         0.021715     0.021715     0.021715        0.021715  ...   
2         0.024377     0.024377     0.024377        0.024377  ...   
3         0.023798     0.023801     0.023799        0.023799  ...   
4         0.021948      0.02196     0.021954         0.02195  ...   
...            ...          ...          ...             ...  ...   
8755      0.029466     0.032902     0.031609        0.029871  ...   
8756      0.030057     0.033401     0.032141        0.030713  ...   
8757      0.029316     0.032575     0.031345        0.030091  ...   
8758      0.030751     0.033824     0.032661        0.031554  ...   
8759      0.032968     0.036106     0.034917        0.033837  ...   

     P221_90_W6_R5 P221_90_W8_R5 P222_0_W6_R5 P222_0_W8_R5 P222_180_W6_R5  \
0              0.0           0.0          0.0          0.0            0.0   
1         0.017407      0.017407     0.017407     0.017407       0.017407   
2         0.019265      0.019265     0.019265     0.019265       0.019265   
3         0.018512      0.018512     0.018512     0.018512       0.018512   
4         0.016733      0.016733     0.016733     0.016733       0.016733   
...            ...           ...          ...          ...            ...   
8755      0.010693      0.010295     0.031551     0.031112       0.030762   
8756      0.012544      0.012024     0.032059     0.031629       0.031566   
8757      0.013658       0.01316      0.03181     0.031389        0.03147   
8758      0.015972      0.015508     0.032487     0.032094       0.032241   
8759      0.017701      0.017232     0.033946     0.033548       0.033741   

     P222_180_W8_R5 P222_270_W6_R5 P222_270_W8_R5 P222_90_W6_R5 P222_90_W8_R5  
0               0.0            0.0            0.0           0.0           0.0  
1          0.017407       0.017407       0.017407      0.017407      0.017407  
2          0.019265       0.019265       0.019265      0.019265      0.019265  
3          0.018512       0.018512       0.018512      0.018512      0.018512  
4          0.016733       0.016733       0.016733      0.016733      0.016733  
...             ...            ...            ...           ...           ...  
8755       0.030332       0.028715       0.028366      0.017829      0.017347  
8756       0.031145       0.029456       0.029123      0.019826       0.01936  
8757        0.03106       0.029408       0.029093      0.020633      0.020181  
8758       0.031855        0.03036       0.030073      0.022492       0.02207  
8759       0.033349       0.031881       0.031598      0.024279      0.023852  

[8760 rows x 84 columns]

In [150]:
def calculate_PE_ht(P_ht, COP, eta_cal, grado_ht, coef_NRPE):
    PE_ht = {}

    for config, dwellings in P_ht.items():
        PE_ht.setdefault(config, {})  # Create an empty dictionary for each outer key in PE_ht
        for dwelling, values in dwellings.items():
            # Perform calculations for PE_ht for each dwelling
            PE_ht[config][dwelling] = [value * (((grado_ht['joule'] + (grado_ht['BC']) / COP) * coef_NRPE['ele']) +
                                              ((grado_ht['caldera_GN'] + grado_ht['nada']) / eta_cal * coef_NRPE['GN']) +
                                              (grado_ht['butano'] / eta_cal * coef_NRPE['butano']))
                                     for value in values]

    return PE_ht


In [151]:
result = calculate_PE_ht(P_ht, COP, eta_cal, grado_ht, coef_NRPE)

In [153]:
PE_ht2 = pd.DataFrame(result)
PE_ht2

BC0_0  \
Dwelling_1  [0.0, 0.021725560902761936, 0.0245716169217695...   

                                                      BC0_180  \
Dwelling_1  [0.0, 0.021725560902761936, 0.0245716169217695...   

                                                      BC0_270  \
Dwelling_1  [0.0, 0.021725560902761936, 0.0245716169217695...   

                                                       BC0_90  \
Dwelling_1  [0.0, 0.021725560902761936, 0.0245716169217695...   

                                                P111_0_W8_R10  \
Dwelling_1  [0.0, 0.02171474307260574, 0.02437654057169146...   

                                                P111_0_W8_R12  \
Dwelling_1  [0.0, 0.02171474300342184, 0.02437653182694835...   

                                                P111_0_W8_R14  \
Dwelling_1  [0.0, 0.021714742973846766, 0.0243765289541458...   

                                                 P111_0_W8_R6  \
Dwelling_1  [0.0, 0.02171474466696584, 0.02437664597921095...   

                                                 P111_0_W8_R8  \
Dwelling_1  [0.0, 0.021714743391190037, 0.0243765671370249...   

                                              P111_180_W8_R10  ...  \
Dwelling_1  [0.0, 0.02171474307260574, 0.02437654057169146...  ...   

                                                P221_90_W6_R5  \
Dwelling_1  [0.0, 0.017406750286469888, 0.0192652747722053...   

                                                P221_90_W8_R5  \
Dwelling_1  [0.0, 0.01740675028022831, 0.01926527340351150...   

                                                 P222_0_W6_R5  \
Dwelling_1  [0.0, 0.017406750055917755, 0.0192652642072097...   

                                                 P222_0_W8_R5  \
Dwelling_1  [0.0, 0.01740675004967615, 0.01926526283851584...   

                                               P222_180_W6_R5  \
Dwelling_1  [0.0, 0.017406750055917755, 0.0192652642072097...   

                                               P222_180_W8_R5  \
Dwelling_1  [0.0, 0.01740675004967615, 0.01926526283851584...   

                                               P222_270_W6_R5  \
Dwelling_1  [0.0, 0.017406750055917755, 0.0192652642072097...   

                                               P222_270_W8_R5  \
Dwelling_1  [0.0, 0.01740675004967615, 0.01926526283851584...   

                                                P222_90_W6_R5  \
Dwelling_1  [0.0, 0.017406750055917755, 0.0192652642072097...   

                                                P222_90_W8_R5  
Dwelling_1  [0.0, 0.01740675004967615, 0.01926526283851584...  

[1 rows x 84 columns]

In [141]:
EER = 2
COP=2 
COP_DHW=1.7 
eta_cal=0.7
coef_CO2={'ele': 0.331, 'GN': 0.252, 'butano': 0.254}
coef_NRPE={'ele': 1.954, 'GN': 1.190, 'butano': 1.201}

def calculate_PE_ht(P_ht, grado_ht, COP, coef_NRPE, eta_cal):
    PE_ht = {}
    
    for i in P_ht:
        PE_ht.setdefault(i, [])
        count = 0
        for j in range(0, len(P_ht[i])):
            PE_value = P_ht[i][count] * (
                ((grado_ht['joule'] + (grado_ht['BC']) / COP) * coef_NRPE['ele']) +
                ((grado_ht['caldera_GN'] + grado_ht['nada']) / eta_cal * coef_NRPE['GN']) +
                (grado_ht['butano'] / eta_cal * coef_NRPE['butano'])
            )
            PE_ht[i].append(PE_value)
            count = count + 1

    return PE_ht



PE_ht_result = calculate_PE_ht(P_ht, grado_ht, COP, coef_NRPE, eta_cal)
print(PE_ht_result)


KeyError: 0

In [73]:
P_ht

{'BC0_0': {'Dwelling_1': [0.0,
   0.013943688146161613,
   0.01577031613303688,
   0.015819811390408996,
   0.015262582061859575,
   0.003969653372767092,
   0.011340362627703519,
   0.020114567865391297,
   0.019796338209640354,
   0.019423308729197553,
   0.006159056495354009,
   0.02132221598859055,
   0.018153159352215186,
   0.01990158574761529,
   0.020288732079677383,
   0.020415484009152017,
   0.021187196336462624,
   0.008494705026428389,
   0.022538150835669398,
   0.011442719594427922,
   0.019686792225199472,
   0.023079678982251193,
   0.004740259417732996,
   0.02649759524514946,
   0.025620596797737726,
   0.028044397317894484,
   0.029340261868487767,
   0.03308944416212284,
   0.0336445562981299,
   0.020026010035809286,
   0.02269394244174368,
   0.015307983689162696,
   0.037593452154285945,
   0.016632246840402064,
   0.044663455064613694,
   0.03536051282192552,
   0.03287900831318343,
   0.03360468190453456,
   0.034275662684190085,
   0.03298638995618194,
   0.0

In [77]:
PE_ht = {}
for i in P_ht:
    PE_ht.setdefault(i, [])
    count = 0
    for j in range(0, len(P_ht[i])):
        PE_ht[i].append(P_ht[i][count]*(((self.grado_ht['joule']+(self.grado_ht['BC'])/COP)*self.coef_NRPE['ele'])+(
                            (self.grado_ht['caldera_GN']+self.grado_ht['nada'])/eta_cal*self.coef_NRPE['GN'])+(self.grado_ht['butano']/eta_cal*self.coef_NRPE['butano'])))
        count = count + 1

KeyError: 0

In [76]:
EER = 2 
COP=2 
COP_DHW=1.7 
eta_cal=0.7

PE_ht = {}

for i in P_ht:
    PE_ht.setdefault(i, [])
    count = 0
    
    for value in P_ht[i]:  # Change the loop variable from j to value
        PE_value = value * (
            ((grado_ht['joule'] + (grado_ht['BC']) / COP) * coef_NRPE['ele']) +
            ((grado_ht['caldera_GN'] + grado_ht['nada']) / eta_cal * coef_NRPE['GN']) +
            (grado_ht['butano'] / eta_cal * coef_NRPE['butano'])
        )
        
        PE_ht[i].append(PE_value)
        count += 1 

TypeError: can't multiply sequence by non-int of type 'float'

In [ ]:
# Iterate through the keys and values of the outer dictionary (i.e., P_ht)
for zone, dwellings in P_ht.items():
    PE_ht.setdefault(zone, {})  # Create an empty dictionary for each outer key in PE_ht
    for dwelling, values in dwellings.items():
        # Perform calculations for PE_ht for each dwelling
        PE_ht[zone][dwelling] = [value * (((grado_ht['joule'] + (grado_ht['BC']) / COP) * coef_NRPE['ele']) + (
            (grado_ht['caldera_GN'] + grado_ht['nada']) / eta_cal * coef_NRPE['GN']) + (grado_ht['butano'] / eta_cal * coef_NRPE['butano']))
            for value in values]

# Now, PE_ht is a dictionary of dictionaries containing the results
print(PE_ht)